<h3 style="text-align: center; font-family: Arial, sans-serif; color: #4CAF50;">Dictionnaire des Datasources</h3>
<table style="width: 100%; border-collapse: collapse; font-family: Arial, sans-serif; font-size: 12pt; text-align: left;">
    <thead>
        <tr style="background-color: #f2f2f2;">
            <th style="border: 1px solid #ddd; padding: 8px; color: #4CAF50; text-align: center; width: 30%;">Nom du Fichier</th>
            <th style="border: 1px solid #ddd; padding: 8px; color: #4CAF50; text-align: center; width: 20%;">Nom du DataFrame</th>
            <th style="border: 1px solid #ddd; padding: 8px; color: #4CAF50; text-align: center; width: 50%;">Description</th>
        </tr>
    </thead>
    <tbody>
        <tr>
            <td style="border: 1px solid #ddd; padding: 1px; text-align: left;">MetroPT3.csv</td>
            <td style="border: 1px solid #ddd; padding: 1px; text-align: center;">df</td>
            <td style="border: 1px solid #ddd; padding: 1px; text-align: left;">Dataset Original</td>
        </tr>
        <tr>
            <td style="border: 1px solid #ddd; padding: 1px; text-align: left;">MetroPT3_corrected.csv</td>
            <td style="border: 1px solid #ddd; padding: 1px; text-align: center;">df</td>
            <td style="border: 1px solid #ddd; padding: 1px; text-align: left;">Dataset avec des observations vides, timestamp avec des gaps de 10 sec respectés avec tag de la panne</td>
        </tr>
    </tbody>
</table>


In [32]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns

# Charger les données
df = pd.read_csv("../Datasources/MetroPT3.csv", delimiter=",", decimal=".", index_col=0)
df.reset_index(drop=True, inplace=True)

In [3]:
# Afficher un apercu des données
display(df)

timestamp    TP2    TP3     H1  DV_pressure  Reservoirs  \
0        2020-02-01 00:00:00 -0.012  9.358  9.340       -0.024       9.358   
1        2020-02-01 00:00:10 -0.014  9.348  9.332       -0.022       9.348   
2        2020-02-01 00:00:19 -0.012  9.338  9.322       -0.022       9.338   
3        2020-02-01 00:00:29 -0.012  9.328  9.312       -0.022       9.328   
4        2020-02-01 00:00:39 -0.012  9.318  9.302       -0.022       9.318   
...                      ...    ...    ...    ...          ...         ...   
1516943  2020-09-01 03:59:10 -0.014  8.918  8.906       -0.022       8.918   
1516944  2020-09-01 03:59:20 -0.014  8.904  8.888       -0.020       8.904   
1516945  2020-09-01 03:59:30 -0.014  8.890  8.876       -0.022       8.892   
1516946  2020-09-01 03:59:40 -0.012  8.876  8.864       -0.022       8.878   
1516947  2020-09-01 03:59:50 -0.014  8.860  8.848       -0.022       8.864   

         Oil_temperature  Motor_current  COMP  DV_eletric  Towers  MPG  LPS  \
0                 53.600         0.0400   1.0         0.0     1.0  1.0  0.0   
1                 53.675         0.0400   1.0         0.0     1.0  1.0  0.0   
2                 53.600         0.0425   1.0         0.0     1.0  1.0  0.0   
3                 53.425         0.0400   1.0         0.0     1.0  1.0  0.0   
4                 53.475         0.0400   1.0         0.0     1.0  1.0  0.0   
...                  ...            ...   ...         ...     ...  ...  ...   
1516943           59.675         0.0425   1.0         0.0     1.0  1.0  0.0   
1516944           59.600         0.0450   1.0         0.0     1.0  1.0  0.0   
1516945           59.600         0.0425   1.0         0.0     1.0  1.0  0.0   
1516946           59.550         0.0450   1.0         0.0     1.0  1.0  0.0   
1516947           59.475         0.0425   1.0         0.0     1.0  1.0  0.0   

         Pressure_switch  Oil_level  Caudal_impulses  
0                    1.0        1.0              1.0  
1                    1.0        1.0              1.0  
2                    1.0        1.0              1.0  
3                    1.0        1.0              1.0  
4                    1.0        1.0              1.0  
...                  ...        ...              ...  
1516943              1.0        1.0              1.0  
1516944              1.0        1.0              1.0  
1516945              1.0        1.0              1.0  
1516946              1.0        1.0              1.0  
1516947              1.0        1.0              1.0  

[1516948 rows x 16 columns]

In [33]:
# Convertir timestamp
df['timestamp'] = pd.to_datetime(df['timestamp'], errors='coerce')
print(df.dtypes)

timestamp          datetime64[ns]
TP2                       float64
TP3                       float64
H1                        float64
DV_pressure               float64
Reservoirs                float64
Oil_temperature           float64
Motor_current             float64
COMP                      float64
DV_eletric                float64
Towers                    float64
MPG                       float64
LPS                       float64
Pressure_switch           float64
Oil_level                 float64
Caudal_impulses           float64
dtype: object


In [34]:
# Filtrer uniquement les colonnes numériques dans un DataFrame
numeric_columns = df.select_dtypes(include=[np.number])

# Ajout des TimeStamp manquants en 2 étapes

In [36]:
#####################
##### Étape 1 : #####
#####################
# Ajuster dabord les timestamp existant pour respecter le gap (saut) de 10 secondes.
def adjust_last_digit_of_seconds(timestamp):
    """Ajuste uniquement le dernier chiffre des secondes du timestamp."""
    seconds = timestamp.second
    last_digit = seconds % 10  # Extraire le dernier chiffre
    
    if 1 <= last_digit <= 5:
        # Arrondir à 0
        adjustment = -last_digit
    elif last_digit > 5:
        # Arrondir au multiple de 10 suivant
        adjustment = 10 - last_digit
    else:
        # Si le dernier chiffre est déjà 0
        adjustment = 0

    # Appliquer l'ajustement aux secondes
    return timestamp + pd.Timedelta(seconds=adjustment)

# Appliquer la correction à tous les timestamps
df['timestamp'] = df['timestamp'].apply(adjust_last_digit_of_seconds)

# Vérification des résultats
print("Aperçu des timestamps corrigés :")
print(df['timestamp'].head())


Aperçu des timestamps corrigés :
0   2020-02-01 00:00:00
1   2020-02-01 00:00:10
2   2020-02-01 00:00:20
3   2020-02-01 00:00:30
4   2020-02-01 00:00:40
Name: timestamp, dtype: datetime64[ns]


In [11]:
#####################
##### Étape 2 : #####
#####################

# Recalculer dynamiquement les intervalles après chaque correction
while True:
    # Calculer les intervalles
    time_diffs = df['timestamp'].diff().dt.total_seconds()

    # Identifier les intervalles problématiques (tout ce qui n'est pas 10 secondes)
    problematic_indices = time_diffs[time_diffs > 10].index

    if len(problematic_indices) == 0:
        print("Toutes les irrégularités ont été corrigées.")
        break

    # Cibler la première irrégularité détectée
    idx = problematic_indices[0]

    # Récupérer le timestamp de départ
    start_time = df.loc[idx - 1, 'timestamp']
    end_time = df.loc[idx, 'timestamp']

    # Calculer les timestamps intermédiaires pour combler l'intervalle
    new_times = pd.date_range(start=start_time, end=end_time, freq='10S', closed='right')

    # Créer un DataFrame avec les nouveaux timestamps
    missing_data = pd.DataFrame({'timestamp': new_times})

    # Ajouter les nouveaux timestamps dans le DataFrame
    df = pd.concat([df, missing_data]).drop_duplicates(subset='timestamp').sort_values('timestamp').reset_index(drop=True)

    # Afficher l'état actuel
    print(f"Correction appliquée à l'intervalle autour de l'index {idx}.")
    print(df.loc[max(idx - 2, 0):min(idx + len(new_times) + 2, len(df) - 1), ['timestamp']])

# Vérification finale
time_diffs_corrected = df['timestamp'].diff().dt.total_seconds()
print("\nStatistiques des intervalles corrigés après correction finale :")
print(f"Min : {time_diffs_corrected.min()} secondes")
print(f"Max : {time_diffs_corrected.max()} secondes")
print(f"Mode (valeur typique) : {time_diffs_corrected.mode()[0]} secondes")
print(f"Nombre d'irrégularités restantes : {(time_diffs_corrected != 10).sum()}")


C:\Users\usermine\AppData\Local\Temp\ipykernel_10708\1956726645.py:21: FutureWarning: Argument `closed` is deprecated in favor of `inclusive`.
  new_times = pd.date_range(start=start_time, end=end_time, freq='10S', closed='right')


Correction appliquée à l'intervalle autour de l'index 4654.
               timestamp
4652 2020-02-01 12:55:20
4653 2020-02-01 12:55:30
4654 2020-02-01 12:55:40
4655 2020-02-01 12:55:50
4656 2020-02-01 12:56:00
4657 2020-02-01 12:56:10
4658 2020-02-01 12:56:20
4659 2020-02-01 12:56:30
4660 2020-02-01 12:56:40
4661 2020-02-01 12:56:50
4662 2020-02-01 12:57:00
4663 2020-02-01 12:57:10
4664 2020-02-01 12:57:20
4665 2020-02-01 12:57:30
4666 2020-02-01 12:57:40
4667 2020-02-01 12:57:50
4668 2020-02-01 12:58:00
4669 2020-02-01 12:58:10
4670 2020-02-01 12:58:20
4671 2020-02-01 12:58:30
4672 2020-02-01 12:58:40
4673 2020-02-01 12:58:50
4674 2020-02-01 12:59:00
4675 2020-02-01 12:59:10
4676 2020-02-01 12:59:20
4677 2020-02-01 12:59:30
4678 2020-02-01 12:59:40
4679 2020-02-01 12:59:50
4680 2020-02-01 13:00:00
4681 2020-02-01 13:00:10
4682 2020-02-01 13:00:20
4683 2020-02-01 13:00:30
4684 2020-02-01 13:00:40
4685 2020-02-01 13:00:50
4686 2020-02-01 13:01:00
4687 2020-02-01 13:01:10


C:\Users\usermine\AppData\Local\Temp\ipykernel_10708\1956726645.py:21: FutureWarning: Argument `closed` is deprecated in favor of `inclusive`.
  new_times = pd.date_range(start=start_time, end=end_time, freq='10S', closed='right')


Correction appliquée à l'intervalle autour de l'index 7081.
               timestamp
7079 2020-02-01 19:39:50
7080 2020-02-01 19:40:00
7081 2020-02-01 19:40:10
7082 2020-02-01 19:40:20
7083 2020-02-01 19:40:30
...                  ...
8372 2020-02-01 23:15:20
8373 2020-02-01 23:15:30
8374 2020-02-01 23:15:40
8375 2020-02-01 23:15:50
8376 2020-02-01 23:16:00

[1298 rows x 1 columns]


C:\Users\usermine\AppData\Local\Temp\ipykernel_10708\1956726645.py:21: FutureWarning: Argument `closed` is deprecated in favor of `inclusive`.
  new_times = pd.date_range(start=start_time, end=end_time, freq='10S', closed='right')


...

Correction appliquée à l'intervalle autour de l'index 1834062.
                  timestamp
1834060 2020-08-31 06:36:40
1834061 2020-08-31 06:36:50
1834062 2020-08-31 06:37:00
1834063 2020-08-31 06:37:10
1834064 2020-08-31 06:37:20
1834065 2020-08-31 06:37:30
1834066 2020-08-31 06:37:40
1834067 2020-08-31 06:37:50
1834068 2020-08-31 06:38:00
1834069 2020-08-31 06:38:10
1834070 2020-08-31 06:38:20
1834071 2020-08-31 06:38:30
1834072 2020-08-31 06:38:40
1834073 2020-08-31 06:38:50
1834074 2020-08-31 06:39:00
1834075 2020-08-31 06:39:10
1834076 2020-08-31 06:39:20
1834077 2020-08-31 06:39:30
1834078 2020-08-31 06:39:40
1834079 2020-08-31 06:39:50
1834080 2020-08-31 06:40:00
1834081 2020-08-31 06:40:10
1834082 2020-08-31 06:40:20
1834083 2020-08-31 06:40:30
1834084 2020-08-31 06:40:40
1834085 2020-08-31 06:40:50
1834086 2020-08-31 06:41:00
1834087 2020-08-31 06:41:10
1834088 2020-08-31 06:41:20
1834089 2020-08-31 06:41:30
1834090 2020-08-31 06:41:40
1834091 2020-08-31 06:41:50
1834092 2020-

C:\Users\usermine\AppData\Local\Temp\ipykernel_10708\1956726645.py:21: FutureWarning: Argument `closed` is deprecated in favor of `inclusive`.
  new_times = pd.date_range(start=start_time, end=end_time, freq='10S', closed='right')


Correction appliquée à l'intervalle autour de l'index 1838972.
                  timestamp
1838970 2020-08-31 20:15:00
1838971 2020-08-31 20:15:10
1838972 2020-08-31 20:15:20
1838973 2020-08-31 20:15:30
1838974 2020-08-31 20:15:40
...                     ...
1840544 2020-09-01 00:37:20
1840545 2020-09-01 00:37:30
1840546 2020-09-01 00:37:40
1840547 2020-09-01 00:37:50
1840548 2020-09-01 00:38:00

[1579 rows x 1 columns]


C:\Users\usermine\AppData\Local\Temp\ipykernel_10708\1956726645.py:21: FutureWarning: Argument `closed` is deprecated in favor of `inclusive`.
  new_times = pd.date_range(start=start_time, end=end_time, freq='10S', closed='right')


Correction appliquée à l'intervalle autour de l'index 1840575.
                  timestamp
1840573 2020-09-01 00:42:10
1840574 2020-09-01 00:42:20
1840575 2020-09-01 00:42:30
1840576 2020-09-01 00:42:40
1840577 2020-09-01 00:42:50
...                     ...
1841263 2020-09-01 02:37:10
1841264 2020-09-01 02:37:20
1841265 2020-09-01 02:37:30
1841266 2020-09-01 02:37:40
1841267 2020-09-01 02:37:50

[695 rows x 1 columns]
Toutes les irrégularités ont été corrigées.

Statistiques des intervalles corrigés après correction finale :
Min : 10.0 secondes
Max : 10.0 secondes
Mode (valeur typique) : 10.0 secondes
Nombre d'irrégularités restantes : 1


In [50]:
# Afficher un apercu des données
display(df)

timestamp   TP2  TP3   H1  DV_pressure  Reservoirs  \
0        2020-02-01 00:00:00 -0.01 9.36 9.34        -0.02        9.36   
1        2020-02-01 00:00:10 -0.01 9.35 9.33        -0.02        9.35   
2        2020-02-01 00:00:20 -0.01 9.34 9.32        -0.02        9.34   
3        2020-02-01 00:00:30 -0.01 9.33 9.31        -0.02        9.33   
4        2020-02-01 00:00:40 -0.01 9.32 9.30        -0.02        9.32   
...                      ...   ...  ...  ...          ...         ...   
1841755  2020-09-01 03:59:10 -0.01 8.92 8.91        -0.02        8.92   
1841756  2020-09-01 03:59:20 -0.01 8.90 8.89        -0.02        8.90   
1841757  2020-09-01 03:59:30 -0.01 8.89 8.88        -0.02        8.89   
1841758  2020-09-01 03:59:40 -0.01 8.88 8.86        -0.02        8.88   
1841759  2020-09-01 03:59:50 -0.01 8.86 8.85        -0.02        8.86   

         Oil_temperature  Motor_current  COMP  DV_eletric  Towers  MPG  LPS  \
0                  53.60           0.04  1.00        0.00    1.00 1.00 0.00   
1                  53.68           0.04  1.00        0.00    1.00 1.00 0.00   
2                  53.60           0.04  1.00        0.00    1.00 1.00 0.00   
3                  53.42           0.04  1.00        0.00    1.00 1.00 0.00   
4                  53.48           0.04  1.00        0.00    1.00 1.00 0.00   
...                  ...            ...   ...         ...     ...  ...  ...   
1841755            59.67           0.04  1.00        0.00    1.00 1.00 0.00   
1841756            59.60           0.04  1.00        0.00    1.00 1.00 0.00   
1841757            59.60           0.04  1.00        0.00    1.00 1.00 0.00   
1841758            59.55           0.04  1.00        0.00    1.00 1.00 0.00   
1841759            59.48           0.04  1.00        0.00    1.00 1.00 0.00   

         Pressure_switch  Oil_level  Caudal_impulses  
0                   1.00       1.00             1.00  
1                   1.00       1.00             1.00  
2                   1.00       1.00             1.00  
3                   1.00       1.00             1.00  
4                   1.00       1.00             1.00  
...                  ...        ...              ...  
1841755             1.00       1.00             1.00  
1841756             1.00       1.00             1.00  
1841757             1.00       1.00             1.00  
1841758             1.00       1.00             1.00  
1841759             1.00       1.00             1.00  

[1841760 rows x 16 columns]

# Ajout de la variable Panne

In [30]:
# Ajouter les classes de panne
# Classe 0 : Pas de panne détectée
# Classe 1 : En pleine panne
# Classe 2 : Panne prévue dans moins de 30 minutes

# Liste des intervalles de pannes
pannes = [
    {'start': '2020-04-18 00:00', 'end': '2020-04-18 23:59'},
    {'start': '2020-05-29 23:30', 'end': '2020-05-30 06:00'},
    {'start': '2020-06-05 10:00', 'end': '2020-06-07 14:30'},
    {'start': '2020-07-15 14:30', 'end': '2020-07-15 19:00'},
         ]

# Convertir les timestamps des pannes en datetime
for panne in pannes:
    panne['start'] = pd.to_datetime(panne['start'])
    panne['end']   = pd.to_datetime(panne['end'])

# Ajouter une colonne 'panne' avec la valeur par défaut 0 (aucune panne détectée)
df['panne'] = 0


for panne in pannes:
    # Classe 1 : En pleine panne
    df.loc[(df['timestamp'] >= panne['start']) & (df['timestamp'] <= panne['end']), 'panne'] = 1
    # Classe 2 : Panne prévue dans moins de 30 minutes
    df.loc[(df['timestamp'] < panne['start']) & (df['timestamp'] >= panne['start'] - pd.Timedelta(minutes=30)), 'panne'] = 2

# Afficher un aperçu du DataFrame avec la nouvelle colonne 'panne'
display(df.head(50))

timestamp   TP2  TP3   H1  DV_pressure  Reservoirs  \
0  2020-02-01 00:00:00 -0.01 9.36 9.34        -0.02        9.36   
1  2020-02-01 00:00:10 -0.01 9.35 9.33        -0.02        9.35   
2  2020-02-01 00:00:20 -0.01 9.34 9.32        -0.02        9.34   
3  2020-02-01 00:00:30 -0.01 9.33 9.31        -0.02        9.33   
4  2020-02-01 00:00:40 -0.01 9.32 9.30        -0.02        9.32   
5  2020-02-01 00:00:50 -0.01 9.31 9.29        -0.02        9.31   
6  2020-02-01 00:01:00 -0.01 9.30 9.28        -0.02        9.30   
7  2020-02-01 00:01:10 -0.01 9.29 9.27        -0.02        9.29   
8  2020-02-01 00:01:20 -0.01 9.28 9.26        -0.02        9.28   
9  2020-02-01 00:01:30 -0.01 9.26 9.25        -0.02        9.26   
10 2020-02-01 00:01:40 -0.01 9.26 9.24        -0.02        9.26   
11 2020-02-01 00:01:50 -0.01 9.25 9.23        -0.02        9.24   
12 2020-02-01 00:02:00 -0.01 9.23 9.22        -0.02        9.23   
13 2020-02-01 00:02:10 -0.01 9.22 9.21        -0.02        9.22   
14 2020-02-01 00:02:20 -0.01 9.21 9.20        -0.02        9.22   
15 2020-02-01 00:02:30 -0.01 9.20 9.19        -0.02        9.20   
16 2020-02-01 00:02:40 -0.01 9.19 9.18        -0.02        9.19   
17 2020-02-01 00:02:50 -0.01 9.18 9.17        -0.02        9.18   
18 2020-02-01 00:03:00 -0.01 9.17 9.16        -0.02        9.17   
19 2020-02-01 00:03:10 -0.01 9.16 9.15        -0.02        9.16   
20 2020-02-01 00:03:20 -0.01 9.15 9.14        -0.02        9.15   
21 2020-02-01 00:03:30 -0.01 9.14 9.13        -0.02        9.14   
22 2020-02-01 00:03:40 -0.01 9.13 9.12        -0.02        9.13   
23 2020-02-01 00:03:50 -0.01 9.12 9.11        -0.02        9.12   
24 2020-02-01 00:04:00 -0.01 9.11 9.09        -0.02        9.11   
25 2020-02-01 00:04:10 -0.01 9.10 9.08        -0.02        9.10   
26 2020-02-01 00:04:20 -0.01 9.09 9.08        -0.02        9.09   
27 2020-02-01 00:04:30 -0.01 9.08 9.07        -0.02        9.08   
28 2020-02-01 00:04:40 -0.01 9.07 9.05        -0.02        9.07   
29 2020-02-01 00:04:50 -0.01 9.06 9.04        -0.02        9.06   
30 2020-02-01 00:05:00 -0.01 9.05 9.04        -0.02        9.05   
31 2020-02-01 00:05:10 -0.01 9.04 9.03        -0.02        9.04   
32 2020-02-01 00:05:20 -0.01 9.03 9.02        -0.02        9.03   
33 2020-02-01 00:05:30 -0.01 9.02 9.01        -0.02        9.02   
34 2020-02-01 00:05:40 -0.01 9.01 9.00        -0.02        9.01   
35 2020-02-01 00:05:50 -0.01 9.00 8.99        -0.02        9.00   
36 2020-02-01 00:06:00 -0.01 8.99 8.98        -0.02        8.99   
37 2020-02-01 00:06:10 -0.01 8.98 8.97        -0.02        8.98   
38 2020-02-01 00:06:20 -0.01 8.97 8.96        -0.02        8.97   
39 2020-02-01 00:06:30 -0.01 8.96 8.95        -0.02        8.96   
40 2020-02-01 00:06:40 -0.01 8.95 8.94        -0.02        8.95   
41 2020-02-01 00:06:50 -0.01 8.94 8.93        -0.02        8.94   
42 2020-02-01 00:07:00 -0.01 8.93 8.92        -0.02        8.93   
43 2020-02-01 00:07:10 -0.01 8.92 8.91        -0.02        8.92   
44 2020-02-01 00:07:20 -0.01 8.91 8.90        -0.02        8.91   
45 2020-02-01 00:07:30 -0.01 8.90 8.89        -0.02        8.90   
46 2020-02-01 00:07:40 -0.01 8.89 8.88        -0.02        8.89   
47 2020-02-01 00:07:50 -0.01 8.88 8.87        -0.02        8.89   
48 2020-02-01 00:08:00 -0.01 8.87 8.86        -0.02        8.88   
49 2020-02-01 00:08:10 -0.01 8.86 8.85        -0.02        8.87   

    Oil_temperature  Motor_current  COMP  DV_eletric  Towers  MPG  LPS  \
0             53.60           0.04  1.00        0.00    1.00 1.00 0.00   
1             53.68           0.04  1.00        0.00    1.00 1.00 0.00   
2             53.60           0.04  1.00        0.00    1.00 1.00 0.00   
3             53.42           0.04  1.00        0.00    1.00 1.00 0.00   
4             53.48           0.04  1.00        0.00    1.00 1.00 0.00   
5             53.50           0.04  1.00        0.00    1.00 1.00 0.00   
6             53.38           0.04  1.00        0.00    1.00 1.00 0.00   
7  

In [31]:
# Enregistrer le dataframe corrigé dans un fichier CSV
df.to_csv("../Datasources/MetroPT3_corrected.csv", index=True)